<a href="https://colab.research.google.com/github/wiatrak2/BScThesis/blob/master/GRL_3D.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Load data

In [1]:
from google.colab import drive
drive.mount('/content/drive')
import sys
sys.path.append('BScThesis/')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
!pip3 install torch torchvision


In [3]:
!git clone https://github.com/wiatrak2/BScThesis

fatal: destination path 'BScThesis' already exists and is not an empty directory.


In [0]:
from importlib import reload 

In [0]:
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

In [0]:
import torchvision
import torchvision.transforms as transforms

In [0]:
import matplotlib.pyplot as plt
import pickle
import sympy
from collections import defaultdict, namedtuple
import copy

In [0]:
from mnist_m import Mnist_M
from datasets_merge import Merge_Datasets
import models
import trainer
import domain_trainer
from test_model import test_model
import plots
import test
import plotly_plots

In [0]:
import plotly
from plotly import tools
from plotly.offline import init_notebook_mode, iplot
import plotly.graph_objs as go

In [0]:
def convertMnist(img):
  img = img.squeeze().numpy()
  return torch.from_numpy(np.tile(img, (3,1,1)))

In [0]:
batch_size=128
num_workers=1

In [0]:
transform=transforms.Compose([
                           transforms.ToTensor(),
                           transforms.Normalize((0.1307,), (0.3081,)),
                           transforms.Lambda(convertMnist)
                       ])

train_set = torchvision.datasets.MNIST(root='./data', train=True, download=True,
                                     transform=transform)
train_loader = torch.utils.data.DataLoader(train_set, batch_size=batch_size,
                                         shuffle=True, num_workers=num_workers)

test_set = torchvision.datasets.MNIST(root='./data', train=False, download=True,
                                     transform=transform)
test_loader = torch.utils.data.DataLoader(test_set, batch_size=batch_size,
                                         shuffle=False, num_workers=num_workers)





In [0]:
log_interval = 100

In [0]:
use_cuda = True
use_cuda = use_cuda and torch.cuda.is_available()
device = torch.device("cuda" if use_cuda else "cpu")

In [0]:
lr = 0.01
momentum=0.9

In [0]:
mnist_m_transform = transforms.Compose([
                           transforms.Normalize(3*[0.1307], 3*[0.3081]),
                       ])
mnist_m_train = Mnist_M('drive/My Drive/BScThesis/keras_mnistm.pkl',
                        transform=mnist_m_transform)
mnist_m_test = Mnist_M('drive/My Drive/BScThesis/keras_mnistm.pkl',train=False,
                     transform=mnist_m_transform)
mnist_m_train_loader = torch.utils.data.DataLoader(mnist_m_train, 
                                                   batch_size=batch_size,
                                         shuffle=True, num_workers=num_workers)
mnist_m_test_loader = torch.utils.data.DataLoader(mnist_m_test,
                                                  batch_size=batch_size,
                                         shuffle=False, num_workers=num_workers)





In [0]:
Models = namedtuple('Models', ['model_f', 'model_c', 'model_d'])
Optims = namedtuple('Optims', ['optim_f', 'optim_c', 'optim_d'])
Criterions = namedtuple('Criterions', ['criterion', 'criterion_domain'])
Loaders = namedtuple('Loaders', ['train_loader', 'train_loader_domain',
                                'source_test_loader', 'target_test_loader',
                                'merged_test_loader'])

In [0]:
mnist_ext_train = Merge_Datasets([train_set, mnist_m_train])
mnist_ext_test = Merge_Datasets([test_set, mnist_m_test])
mnist_ext_train_loader = torch.utils.data.DataLoader(mnist_ext_train, 
                                                   batch_size=batch_size,
                                         shuffle=True, num_workers=num_workers)
mnist_ext_test_loader = torch.utils.data.DataLoader(mnist_ext_test, 
                                                   batch_size=batch_size,
                                         shuffle=True, num_workers=num_workers)






In [0]:
loaders = Loaders(train_loader, mnist_m_train_loader,
                 test_loader, mnist_m_test_loader, mnist_ext_test_loader)

In [0]:
criterion = F.nll_loss
criterion_domain = F.nll_loss

In [0]:
criterions = Criterions(criterion, criterion_domain)

In [0]:
epochs=10

# Model training

In [0]:
model_f_3_layer = nn.Sequential(nn.Linear(320,3))
model_f_gr = models.extend_feature_extractor(models.MnistFeatureExtractor(), 
                                         model_f_3_layer, False, False).to(device)
model_c_gr = models.MnistClassPredictor(input_size=3).to(device)
model_d_gr = models.MnistDomain(input_size=3).to(device)

In [0]:
optim_f_gr = optim.SGD(model_f_gr.parameters(), lr=lr, momentum=momentum, nesterov=True)
optim_c_gr = optim.SGD(model_c_gr.parameters(), lr=lr, momentum=momentum, nesterov=True)
optim_d_gr = optim.SGD(model_d_gr.parameters(), lr=lr, momentum=momentum, nesterov=True)

In [0]:
train_models_gr = Models(model_f_gr, model_c_gr, model_d_gr)
optims_gr = Optims(optim_f_gr, optim_c_gr, optim_d_gr)

In [0]:
model_trainer_gr = trainer.Trainer(train_models_gr, optims_gr, criterions, device,
                                train_domain=True, tune_lr=True)

In [66]:
test_history_gr = defaultdict(lambda:[])
model_trainer_gr.train(epochs, loaders, test_history=test_history_gr)

Train Epoch: 					1 [0/60000 (0%)]	Loss: 1.352741, lr: 0.01000 lambd: 0.00000
Train Epoch: 					1 [12800/60000 (21%)]	Loss: 0.989797, lr: 0.00425 lambd: 0.78820
Train Epoch: 					1 [25600/60000 (43%)]	Loss: 1.076459, lr: 0.00288 lambd: 0.97233
Train Epoch: 					1 [38400/60000 (64%)]	Loss: 0.891899, lr: 0.00223 lambd: 0.99668
Train Epoch: 					1 [51200/60000 (85%)]	Loss: 0.950772, lr: 0.00184 lambd: 0.99961

Target Domain Test set: Average loss: 2.2502, Accuracy: 3782/10000 (38%)
Source Domain Test set: Average loss: 0.5173, Accuracy: 8446/10000 (84%)
Domains predictor:  Accuracy: 12979/20000 (65%)



In [0]:
best_mf_gr = copy.deepcopy(model_trainer_gr.best_model.model_f)

In [0]:
def get_input_mtx(loader, model, c_size):
  X = np.zeros(c_size).T
  for batch_idx, (data, labels) in enumerate(loader):
    data = data.to(device)
    idx = batch_idx * loader.batch_size
    X[idx:idx+loader.batch_size] = model(data).cpu().detach().numpy()
  return X.T

In [0]:
X_gr = get_input_mtx(test_loader, best_mf_gr, (3, len(test_set)))

In [0]:
X_m_gr = get_input_mtx(mnist_m_test_loader, best_mf_gr, (3, len(test_set)))

In [0]:
X_m_gr2 = get_input_mtx(mnist_m_test_loader, model_f_gr, (3, len(test_set)))

In [0]:
[x,y,z] = X_gr
trace1 = go.Scatter3d(x=x,y=y,z=z, mode='markers', marker=dict(
        size=12,line=dict(color='rgba(217, 217, 217, 0.14)',width=0.5),opacity=0.8))

[x2, y2, z2] = X_m_gr
trace2 = go.Scatter3d(x=x2,y=y2,z=z2,mode='markers',marker=dict(
        color='rgb(127, 127, 127)',size=12,symbol='circle',line=dict(color='rgb(204, 204, 204)',width=1),opacity=0.9))

[x3, y3, z3] = X_m_gr2
trace3 = go.Scatter3d(x=x3,y=y3,z=z3,mode='markers',marker=dict(color='rgb(255, 255, 204)',
        size=12,symbol='circle',line=dict(color='rgb(255, 255, 20)',width=1),opacity=0.9))


data = [trace1, trace2, trace3]
layout = go.Layout(margin=dict(l=0,r=0,b=0,t=0))
fig = go.Figure(data=data, layout=layout)

plotly_plots.configure_plotly_browser_state()

init_notebook_mode(connected=False)

fig['layout'].update(height=800, width=1200, title='MNIST')
plotly.offline.iplot(fig, filename='basic-line')

# Fixed lambda coefficient

In [0]:
model_f_3_layer_fix = nn.Sequential(nn.Linear(320,3))
model_f_gr_fix = models.extend_feature_extractor(models.MnistFeatureExtractor(), 
                                         model_f_3_layer_fix, False, False).to(device)
model_c_gr_fix = models.MnistClassPredictor(input_size=3).to(device)
model_d_gr_fix = models.MnistDomain(input_size=3).to(device)

In [0]:
optim_f_gr_fix = optim.SGD(model_f_gr_fix.parameters(), lr=lr, momentum=momentum, nesterov=True)
optim_c_gr_fix = optim.SGD(model_c_gr_fix.parameters(), lr=lr, momentum=momentum, nesterov=True)
optim_d_gr_fix = optim.SGD(model_d_gr_fix.parameters(), lr=lr, momentum=momentum, nesterov=True)

In [0]:
train_models_gr_fix = Models(model_f_gr_fix, model_c_gr_fix, model_d_gr_fix)
optims_gr_fix = Optims(optim_f_gr_fix, optim_c_gr_fix, optim_d_gr_fix)

In [0]:
model_trainer_gr_fix = trainer.Trainer(train_models_gr_fix, optims_gr_fix, criterions, device,
                                train_domain=True, tune_lr=True, use_lambd=False,
                                  default_lambd=0.4)

In [0]:
test_history_gr_fix = defaultdict(lambda:[])
model_trainer_gr_fix.train(8, loaders, test_history=test_history_gr_fix)

Train Epoch: 					1 [0/60000 (0%)]	Loss: 2.324380, lr: 0.01000 lambd: 0.40000
Train Epoch: 					1 [12800/60000 (21%)]	Loss: 0.996758, lr: 0.00838 lambd: 0.40000
Train Epoch: 					1 [25600/60000 (43%)]	Loss: 0.574016, lr: 0.00726 lambd: 0.40000
Train Epoch: 					1 [38400/60000 (64%)]	Loss: 0.629152, lr: 0.00643 lambd: 0.40000
Train Epoch: 					1 [51200/60000 (85%)]	Loss: 0.580396, lr: 0.00580 lambd: 0.40000

Target Domain Test set: Average loss: 3.5707, Accuracy: 4564/10000 (46%)
Source Domain Test set: Average loss: 0.2496, Accuracy: 9253/10000 (93%)
Domains predictor:  Accuracy: 11480/20000 (57%)

Train Epoch: 					2 [0/60000 (0%)]	Loss: 0.396674, lr: 0.00544 lambd: 0.40000
Train Epoch: 					2 [12800/60000 (21%)]	Loss: 0.320739, lr: 0.00500 lambd: 0.40000
Train Epoch: 					2 [25600/60000 (43%)]	Loss: 0.582120, lr: 0.00464 lambd: 0.40000
Train Epoch: 					2 [38400/60000 (64%)]	Loss: 0.269440, lr: 0.00433 lambd: 0.40000
Train Epoch: 					2 [51200/60000 (85%)]	Loss: 0.282333, lr: 0.00407

# Plot with digits distinction

In [0]:
def plot_digits(X, labels):
  data = []
  for i in range(len(set(labels))):
    _X = X[:, labels==i]
    [x, y, z] = _X
    trace = go.Scatter3d(x=x,y=y,z=z, name='{}'.format(i), mode = 'markers',marker = dict(
        size = 10,color = i,line = dict(width = 2,color = i, colorscale='Viridis')))
    data.append(trace)
    
  layout = dict(title = 'Styled Scatter',
                yaxis = dict(zeroline = False),
                xaxis = dict(zeroline = False)
               )

  fig = dict(data=data, layout=layout)
  plotly_plots.configure_plotly_browser_state()

  init_notebook_mode(connected=False)

  fig['layout'].update(height=800, width=1200, title='DIGITS')
  plotly.offline.iplot(fig, filename='scatter')

In [0]:
X_labels = np.array([test_set[i][1] for i in range(len(test_set))])

In [0]:
X_m_labels = np.array([mnist_m_test[i][1] for i in range(len(mnist_m_test))])

In [0]:
plot_digits(X_gr, X_labels)

In [0]:
plot_digits(X_m_gr, X_m_labels)

# Model without 3-dimensional layer

In [0]:
model_f_adam = models.MnistFeatureExtractor().to(device)
model_c_adam = models.MnistClassPredictor().to(device)
model_d_adam = models.MnistDomain().to(device)
lr=0.001
adam_f = optim.Adam(model_f_adam.parameters(), lr=lr)
adam_c = optim.Adam(model_c_adam.parameters(), lr=lr)
adam_d = optim.Adam(model_d_adam.parameters(), lr=lr)

adam_models = Models(model_f_adam, model_c_adam, model_d_adam)
adam_optims = Optims(adam_f, adam_c, adam_d)

In [0]:
adam_trainer = trainer.Trainer(adam_models, adam_optims, criterions, device, train_domain=False)

In [69]:
adam_test_history = defaultdict(lambda:[])
adam_trainer.train(epochs, loaders, test_history=adam_test_history)

Train Epoch: 					1 [0/60000 (0%)]	Loss: 2.304590, lr: 0.00000 lambd: 1.00000
Train Epoch: 					1 [12800/60000 (21%)]	Loss: 0.457894, lr: 0.00000 lambd: 1.00000
Train Epoch: 					1 [25600/60000 (43%)]	Loss: 0.339480, lr: 0.00000 lambd: 1.00000
Train Epoch: 					1 [38400/60000 (64%)]	Loss: 0.258585, lr: 0.00000 lambd: 1.00000
Train Epoch: 					1 [51200/60000 (85%)]	Loss: 0.154358, lr: 0.00000 lambd: 1.00000

Target Domain Test set: Average loss: 1.4826, Accuracy: 5162/10000 (52%)
Source Domain Test set: Average loss: 0.0905, Accuracy: 9725/10000 (97%)
Domains predictor:  Accuracy: 11317/20000 (57%)

Train Epoch: 					2 [0/60000 (0%)]	Loss: 0.182043, lr: 0.00000 lambd: 1.00000
Train Epoch: 					2 [12800/60000 (21%)]	Loss: 0.308072, lr: 0.00000 lambd: 1.00000
Train Epoch: 					2 [25600/60000 (43%)]	Loss: 0.274313, lr: 0.00000 lambd: 1.00000
Train Epoch: 					2 [38400/60000 (64%)]	Loss: 0.174122, lr: 0.00000 lambd: 1.00000
Train Epoch: 					2 [51200/60000 (85%)]	Loss: 0.196096, lr: 0.00000

## Conceptor functions

In [0]:
def get_conceptor(X, alpha):
  R = np.matmul(X, X.T) * (1/X.shape[0])
  IdX = np.identity(X.shape[0])
  return np.matmul(R, np.linalg.inv((R + alpha**(-2) * IdX)))

In [0]:
def quota(C):
  U, S, U_T = np.linalg.svd(C)
  return np.sum(S) / len(S)

In [0]:
X = get_input_mtx(test_loader, model_f_adam, (320, len(test_set)))

In [0]:
X_m = get_input_mtx(mnist_m_test_loader, model_f_adam, (320, len(test_set)))

In [0]:
C_m = get_conceptor(X_m, 0.7)

In [37]:
quota(C_m)

0.6989398067174799

## Model with conceptor filter

In [0]:
model_f_conc = copy.deepcopy(model_f_adam)

In [0]:
model_conc = models.ConceptorModel(model_f_conc, C_m, device)
optim_conc = optim.Adam(model_conc.parameters(), lr=lr)
train_models_conc = Models(model_conc, model_c_adam, model_d_adam)
optims_conc = Optims(optim_conc, adam_c, adam_d)
model_conc_trainer = trainer.Trainer(train_models_conc, optims_conc, criterions, device,
                                train_domain=False)

In [45]:
test_c_history = defaultdict(lambda:[])
model_conc_trainer.train(epochs, loaders, test_history=test_c_history)

Train Epoch: 					1 [0/60000 (0%)]	Loss: 0.095419, lr: 0.00000 lambd: 1.00000
Train Epoch: 					1 [12800/60000 (21%)]	Loss: 0.122739, lr: 0.00000 lambd: 1.00000
Train Epoch: 					1 [25600/60000 (43%)]	Loss: 0.109158, lr: 0.00000 lambd: 1.00000
Train Epoch: 					1 [38400/60000 (64%)]	Loss: 0.083030, lr: 0.00000 lambd: 1.00000
Train Epoch: 					1 [51200/60000 (85%)]	Loss: 0.066299, lr: 0.00000 lambd: 1.00000

Target Domain Test set: Average loss: 1.3438, Accuracy: 5711/10000 (57%)
Source Domain Test set: Average loss: 0.0328, Accuracy: 9900/10000 (99%)
Domains predictor:  Accuracy: 10483/20000 (52%)

Train Epoch: 					2 [0/60000 (0%)]	Loss: 0.026102, lr: 0.00000 lambd: 1.00000
Train Epoch: 					2 [12800/60000 (21%)]	Loss: 0.088662, lr: 0.00000 lambd: 1.00000
Train Epoch: 					2 [25600/60000 (43%)]	Loss: 0.122704, lr: 0.00000 lambd: 1.00000
Train Epoch: 					2 [38400/60000 (64%)]	Loss: 0.215848, lr: 0.00000 lambd: 1.00000
Train Epoch: 					2 [51200/60000 (85%)]	Loss: 0.101947, lr: 0.00000

In [0]:
model_test = nn.Sequential(model_f_conc, model_c_adam)

In [47]:
test_model(model_test, device, criterions, mnist_m_test_loader)


Test set: Average loss: 1.3637, Accuracy: 5529/10000 (55%)



In [0]:
C = get_conceptor(X, 0.7)

In [72]:
quota(C)

0.8558900002500271

In [0]:
model_conc = models.ConceptorModel(model_f_conc, C, device)

In [0]:
model_test = nn.Sequential(model_conc, model_c_adam)

In [75]:
test_model(model_test, device, criterions, mnist_m_test_loader)


Test set: Average loss: 1.3866, Accuracy: 5656/10000 (57%)

